# Source code to generate data

In [7]:
import numpy as np, random as rd, networkx as nx, copy, os
import multiprocess as mp
from multiprocessing import Pool

Initial state. For the star graph, node 0 is center whereas node 1 to N-1 are the leaves.

In [3]:
def initial_state(N,r):  # N is the population size, r is relative mutant fitness.  The population is initialised with mutant at node 0. 
    state=np.zeros((N,2),dtype='float')
    state[:,0]=int(0)
    state[:,1]=1
    state[0,0]=int(1)
    state[0,1]=r
    return state;

In [4]:
def state_update_dB_star(state,r,N):  # state update for the Moran death Birth process
    state_copy = copy.deepcopy(state)
    death_pos=rd.randrange(N)
    if(death_pos==0):
        total_fitness=np.sum(state_copy[1:,1])
        rel_fitness=state_copy[1:,1]/total_fitness
        neighbours=np.arange(1,N,1,dtype='int')
        birth_pos=rd.choices(neighbours, weights=rel_fitness, cum_weights=None, k=1)[0]
        state_copy[death_pos,0]=state_copy[birth_pos,0] 
        state_copy[death_pos,1]=state_copy[birth_pos,1]       
    else:
        state_copy[death_pos,0]=state_copy[0,0] 
        state_copy[death_pos,1]=state_copy[0,1]   
    return state_copy;

Below, we generate the data for the fixation probability on the star graph under dB updating, given that the mutant starts from the central node. To generate data for the leaf initialsation, please make a corresponding change in the initial state function above, and then run the code below.

In [ ]:
# Parameters used here are the same as in the paper. 
#Warning: It might get very slow to work with these parameters. Please change parameters at your convenience. 


N=100
r=np.concatenate((np.arange(0.2,2,0.2),np.arange(2,9.8,0.5)))
Trials=2000

fix_prob=np.zeros(np.size(r))
for j in range(np.size(r)):
    counter=0
    for i in range(Trials):
        num_mutants=1
        flag=1
        old_state=initial_state(N,r[j])
        while(num_mutants<N):
            new_state=copy.deepcopy(state_update_dB_star(old_state,r[j],N))
            old_state=copy.deepcopy(new_state)
            num_mutants=np.sum(old_state[:,0])
            if(num_mutants==0):
                flag=0
                break
        counter=counter+flag
    fix_prob[j]=counter/Trials       
    print(r[j],fix_prob[j])

In [10]:
### Uncomment below only if you want to overwrite the exsiting data.  
# path=os.getcwd()
# subpath1='/Data/Fig_2/'    # Path to the directory where data will be saved.
# np.save(path+subpath1+'star_center_N_{}_Trials_{}.npy'.format(N,Trials),fix_prob) 